In [1]:
import pandas as pd

In [2]:
job_companies = pd.read_csv('data/job_companies.csv')
job_tags = pd.read_csv('data/job_tags.csv')
tags = pd.read_csv('data/tags.csv')
train = pd.read_csv('data/train.csv')
user_tags = pd.read_csv('data/user_tags.csv')

In [9]:
tag_keyword = {}
for i,row in tags.iterrows():
    tag_keyword[row['tagID']] = row['keyword']

In [11]:
avg_sizes = []
job_company = {}
for i,row in job_companies.iterrows():
    sizes = str(row['companySize']).split("-")
    avg_size = -1
    if len(sizes)>1:
        avg_size = (int(sizes[0])+int(sizes[1]))/2
    avg_sizes.append(avg_size)
    job_company[row['jobID']] = row['companyID']
    

job_companies['companySize'] = avg_sizes    
job_companies.head()

companyID                             jobID  \
0  00411460f7c92d2124a67ea0f4cb5f85  e5f6ad6ce374177eef023bf5d0c018b6   
1  1905aedab9bf2477edc068a355bba31a  185e65bc40581880c4f2c82958de8cfe   
2  89fcd07f20b6785b92134bd6c1d0fa42  0537fb40a68c18da59a35c2bfe1ca554   
3  acf4b89d3d503d8252c9c4ba75ddbf6d  b7ee6f5f9aa5cd17ca1aea43ce848496   
4  fb7b9ffa5462084c5f4e7e85a093e6d7  efe937780e95574250dabe07151bdc23   

   companySize  
0         -1.0  
1         30.5  
2        150.5  
3          5.5  
4         -1.0

In [12]:
jobs_tags = {}
for i,row in job_tags.iterrows():
    if row['jobID'] in jobs_tags:
        jobs_tags[row['jobID']].append(tag_keyword[row['tagID']])
    else:
        jobs_tags[row['jobID']] = [tag_keyword[row['tagID']]]
print(jobs_tags)

{'320722549d1751cf3f247855f937b982': ['Ruby', 'Ruby on Rails'], 'e744f91c29ec99f0e662c9177946c627': ['Node.js', 'JavaScript', 'Git'], 'e820a45f1dfc7b95282d10b6087e11c0': ['HTML', 'Vue.js', 'AngularJS', 'JavaScript', 'CSS', 'ReactJS'], '53c3bce66e43be4f209556518c2fcb54': ['Apache Spark', 'Apache Hadoop'], 'fd06b8ea02fe5b1c2496fe1700e9d16c': ['Django', 'Docker', 'AWS EC2', 'JavaScript', 'BitBucket', 'Python', 'Node.js', 'PostgreSQL', 'Git', 'Redis'], '6e7d2da6d3953058db75714ac400b584': ['Java', 'SQL', 'Node.js', 'TypeScript', 'Webpack', 'REST API', 'MySQL', 'Amazon Web Services(AWS)', 'ExpressJS', 'Angular'], '818f4654ed39a1c147d1e51a00ffb4cb': ['Webpack', 'ReactJS', 'TypeScript', 'Git', 'Node.js', 'ES6', 'JavaScript', 'Next.js', 'Redux-Saga'], '019d385eb67632a7e958e23f24bd07d7': ['Python'], '8757150decbd89b0f5442ca3db4d0e0e': ['Java', 'Spring Boot', 'JavaScript', 'Ionic', 'ES6', 'Angular'], '3871bd64012152bfb53fdf04b401193f': ['CSS', 'JavaScript', 'React Native', 'HTML'], '1651cf0d2f737

In [22]:
size_tech = {'none':{}, 'small':{},'medium':{},'big':{}}    #Nan, 0~10, 11~100, 100~
size_class = []
company_size = {}
for i, row in job_companies.iterrows():
    techs = jobs_tags[row['jobID']]
    companySize = row['companySize']
    
    if companySize<0:
        size_class.append(0)
    elif companySize<10:
        size_class.append(1)
    elif companySize<100:
        size_class.append(2)
    else:
        size_class.append(3)
    
    company_size[row['companyID']] = size_class[i]
    
    for tech in techs: 
        if companySize<0:    #NaN
            if tech in size_tech['none']:
                size_tech['none'][tech]+=1
            else:
                size_tech['none'][tech]=1

        elif companySize<10:    #small
            if tech in size_tech['small']:
                size_tech['small'][tech]+=1
            else:
                size_tech['small'][tech]=1

        elif companySize<100:
            if tech in size_tech['medium']:
                size_tech['medium'][tech]+=1
            else:
                size_tech['medium'][tech]=1

        else:
            if tech in size_tech['big']:
                size_tech['big'][tech]+=1
            else:
                size_tech['big'][tech]=1

job_companies['size_class'] = size_class
for key in size_tech.keys():
    size_tech[key] = sorted(size_tech[key].items(),key=lambda x:x[1],reverse=True)



In [18]:
user_tech = {}

for i,row in user_tags.iterrows():
    userID = row['userID']
    tag = tag_keyword[row['tagID']]
    if userID in user_tech:
        user_tech[userID].add(tag)
    else:
        user_tech[userID] = set([tag])
    

In [19]:
wgraph = {}
for row in user_tech.items():
    lrow = list(row[1])
    for i in range(len(lrow)):
        if lrow[i] in wgraph:
            for j in range(i+1,len(lrow)):
                if lrow[j] in wgraph[lrow[i]]:
                    wgraph[lrow[i]][lrow[j]]+=1
                else:
                    wgraph[lrow[i]][lrow[j]]=1
        else:
            wgraph[lrow[i]] = {}
            for j in range(i+1,len(lrow)):
                if lrow[j] in wgraph[lrow[i]]:
                    wgraph[lrow[i]][lrow[j]]+=1
                else:
                    wgraph[lrow[i]][lrow[j]]=1
for key in wgraph.keys():
    wgraph[key] = sorted(wgraph[key].items(),key=lambda x:x[1],reverse=True)
print(wgraph)

{'Spring Cloud': [('MQTT', 1), ('Naver Cloud Platform', 1), ('JUnit', 1), ('Redis', 1), ('Jenkins', 1), ('Apache Kafka', 1), ('JavaScript', 1), ('Zuul', 1), ('WebSocket', 1), ('MyBatis', 1), ('Spring Data JPA', 1), ('Git', 1), ('Java', 1), ('Regular expression', 1), ('Spring', 1), ('i18n', 1), ('Vuex', 1), ('MariaDB', 1), ('ES6', 1), ('OAuth', 1), ('Vue.js', 1), ('Spring Boot', 1), ('GitHub', 1), ('Docker', 1), ('Apache Subversion(SVN)', 1)], 'MQTT': [('Git', 4), ('JavaScript', 3), ('Spring', 3), ('Jenkins', 2), ('MyBatis', 2), ('Java', 2), ('MariaDB', 2), ('Vue.js', 2), ('Spring Boot', 2), ('Docker', 2), ('SQLite', 2), ('Raspberry Pi', 2), ('Android', 2), ('MongoDB', 2), ('Naver Cloud Platform', 1), ('JUnit', 1), ('Redis', 1), ('Apache Kafka', 1), ('Zuul', 1), ('WebSocket', 1), ('Spring Data JPA', 1), ('Regular expression', 1), ('i18n', 1), ('Vuex', 1), ('ES6', 1), ('OAuth', 1), ('GitHub', 1), ('Apache Subversion(SVN)', 1), ('C', 1), ('C++', 1), ('ExpressJS', 1), ('RabbitMQ', 1), ('Am

In [20]:
count = 0
for elem in user_tech.items():
    print(list(elem[1]))

['Spring Cloud', 'MQTT', 'Naver Cloud Platform', 'JUnit', 'Redis', 'Jenkins', 'Apache Kafka', 'JavaScript', 'Zuul', 'WebSocket', 'MyBatis', 'Spring Data JPA', 'Git', 'Java', 'Regular expression', 'Spring', 'i18n', 'Vuex', 'MariaDB', 'ES6', 'OAuth', 'Vue.js', 'Spring Boot', 'GitHub', 'Docker', 'Apache Subversion(SVN)']
['.NET', 'MVC', 'Linux', 'Raspberry Pi', 'Tensorflow', 'Android', 'IoT', 'Python']
['Oracle', 'Java', 'MSSQL(Microsoft SQL Server)', 'JSP', 'MyBatis', 'Git', 'JIRA']
['centOS', 'Spring Batch', 'Shell Script', 'RabbitMQ', 'Redis', 'Apache Subversion(SVN)', 'Spring', 'Jenkins', 'Shell', 'PostgreSQL']
['Travis CI', 'AWS S3', 'AWS EC2', 'Heroku', 'Nginx', 'Ubuntu', 'CSS3', 'Redis', 'MongoDB Atlas', 'Vanilla JS', 'Bootstrap', 'Passport.js', 'MongoDB', 'TensorFlow.js', 'Sequelize.js', 'ExpressJS', 'React Hooks API', 'AWS ElasticBeanstalk', 'Socket.IO', 'AWS CloudWatch', 'Pug', 'Git', 'HTML5', 'AWS ElastiCache', 'AWS RDS', 'MySQL', 'Material-UI', 'OAuth', 'Node.js', 'JWT', 'Reac

In [52]:
majorstacks_col = []
minorstacks_col = []
companySize_col = []
companystacks_col = []
mystacks_col = []

for i,row in train.iterrows():
    userID = row['userID']
    jobID = row['jobID']
    mystacks = user_tech[userID]
    companystacks = jobs_tags[jobID]
    majorstacks = 0
    minorstack = {}
    minorstacks = 0
    

    
    for stack in mystacks:
        minors = wgraph[stack]
        for sname,weight in minors:
            if sname in minorstack:
                minorstack[sname]+=weight
            else:
                minorstack[sname]=weight
        
        if stack in companystacks:
            majorstacks+=1
    
    minorstack_sorted = sorted(minorstack.items(),key=lambda x:x[1],reverse=True)
    minorstack = []
    for stack in minorstack_sorted:
        if stack[0] not in mystacks:
            minorstack.append(stack[0])
            if len(minorstack)==10:
                break
    
    for stack in minorstack:
        if stack in companystacks:
            minorstacks+=1
    companySize = company_size[job_company[jobID]]
    
    companySize_col.append(companySize)
    majorstacks_col.append(majorstacks)
    minorstacks_col.append(minorstacks)
    mystacks_col.append(len(mystacks))
    companystacks_col.append(len(companystacks))


In [55]:
train_set = pd.DataFrame({'majorstacks/mystacks':[],'majorstacks/companystacks':[],'companySize':[],
                          'minorstacks/companystacks':[],'majorstacks':[],'minorstacks':[]})
train_set['mystacks'] = mystacks_col
train_set['companystacks'] = companystacks_col
train_set['companySize'] = companySize_col
train_set['majorstacks'] = majorstacks_col
train_set['minorstacks'] = minorstacks_col
train_set['majorstacks/mystacks'] = train_set['majorstacks']/train_set['mystacks']
train_set['majorstacks/companystacks'] = train_set['majorstacks']/train_set['companystacks']
train_set['minorstacks/companystacks'] = train_set['minorstacks']/train_set['companystacks']
train_set['applied'] = train['applied']

train_set.drop('companystacks',axis=1)

majorstacks/mystacks  majorstacks/companystacks  companySize  \
0                 0.000000                   0.000000            2   
1                 0.040000                   0.333333            3   
2                 0.142857                   0.333333            0   
3                 0.176471                   0.600000            2   
4                 0.050000                   0.250000            2   
...                    ...                        ...          ...   
5995              0.068966                   1.000000            2   
5996              0.120000                   0.500000            2   
5997              0.142857                   0.166667            3   
5998              0.142857                   0.250000            2   
5999              0.037037                   0.250000            3   

      minorstacks/companystacks  majorstacks  minorstacks  mystacks  applied  
0                      0.000000            0            0        13        0  
1                      0.333333            1            1        25        0  
2                      0.000000            1            0         7        1  
3                      0.000000            3            0        17        0  
4                      0.500000            1            2        20        0  
...                         ...          ...          ...       ...      ...  
5995                   0.000000            2            0        29        0  
5996                   0.333333            3            2        25        0  
5997                   0.166667            2            2        14        0  
5998                   0.250000            1            1         7        0  
5999                   0.250000            1            1        27        0  

[6000 rows x 8 columns]

In [57]:
import numpy as np
X = np.array(pd.DataFrame(train_set, columns=['majorstacks/mystacks','majorstacks/companystacks', 'companySize', 
                                                'minorstacks/companystacks','majorstacks','minorstacks','mystacks']))
y = np.array(pd.DataFrame(train_set, columns=['applied']))

In [59]:
from sklearn.tree import DecisionTreeClassifier
dtree = DecisionTreeClassifier()
dtree = dtree.fit(X, y)

In [63]:
test = pd.read_csv('data/test_job.csv')
majorstacks_col = []
minorstacks_col = []
companySize_col = []
companystacks_col = []
mystacks_col = []

for i,row in test.iterrows():
    userID = row['userID']
    jobID = row['jobID']
    mystacks = user_tech[userID]
    companystacks = jobs_tags[jobID]
    majorstacks = 0
    minorstack = {}
    minorstacks = 0
    

    
    for stack in mystacks:
        minors = wgraph[stack]
        for sname,weight in minors:
            if sname in minorstack:
                minorstack[sname]+=weight
            else:
                minorstack[sname]=weight
        
        if stack in companystacks:
            majorstacks+=1
    
    minorstack_sorted = sorted(minorstack.items(),key=lambda x:x[1],reverse=True)
    minorstack = []
    for stack in minorstack_sorted:
        if stack[0] not in mystacks:
            minorstack.append(stack[0])
            if len(minorstack)==10:
                break
    
    for stack in minorstack:
        if stack in companystacks:
            minorstacks+=1
    companySize = company_size[job_company[jobID]]
    
    companySize_col.append(companySize)
    majorstacks_col.append(majorstacks)
    minorstacks_col.append(minorstacks)
    mystacks_col.append(len(mystacks))
    companystacks_col.append(len(companystacks))

test_set = pd.DataFrame({'majorstacks/mystacks':[],'majorstacks/companystacks':[],'companySize':[],
                          'minorstacks/companystacks':[],'majorstacks':[],'minorstacks':[]})
test_set['mystacks'] = mystacks_col
test_set['companystacks'] = companystacks_col
test_set['companySize'] = companySize_col
test_set['majorstacks'] = majorstacks_col
test_set['minorstacks'] = minorstacks_col
test_set['majorstacks/mystacks'] = test_set['majorstacks']/test_set['mystacks']
test_set['majorstacks/companystacks'] = test_set['majorstacks']/test_set['companystacks']
test_set['minorstacks/companystacks'] = test_set['minorstacks']/test_set['companystacks']
test_set = test_set.drop('companystacks',axis=1)
test_set.head()

majorstacks/mystacks  majorstacks/companystacks  companySize  \
0              0.230769                   0.428571            2   
1              0.083333                   0.142857            2   
2              0.166667                   0.142857            2   
3              0.000000                   0.000000            2   
4              0.000000                   0.000000            2   

   minorstacks/companystacks  majorstacks  minorstacks  mystacks  
0                   0.142857            3            1        13  
1                   0.142857            1            1        12  
2                   0.142857            1            1         6  
3                   0.000000            0            0         5  
4                   0.666667            0            4        11

In [72]:
import collections
test_X = np.array(pd.DataFrame(test_set, columns=['majorstacks/mystacks','majorstacks/companystacks', 'companySize', 
                                                'minorstacks/companystacks','majorstacks','minorstacks','mystacks']))
prediction = dtree.predict(test_X)
collections.Counter(prediction)
result = pd.DataFrame({'applied':prediction})
result.to_csv('predict.csv',index=False)

In [79]:
from IPython.display import Image
from sklearn import tree
import pydotplus
feature_names = train_set.columns.tolist()
feature_names = feature_names[0:7]
target_name = np.array(['apllied No', 'applied Yes'])
dt_dot_data = tree.export_graphviz(dtree, out_file = None,
                                  feature_names = feature_names,
                                  class_names = target_name,
                                  filled = True, rounded = True,
                                  special_characters = True)
dt_graph = pydotplus.graph_from_dot_data(dt_dot_data)
Image(dt_graph.create_png())


dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.407271 to fit



In [81]:
from sklearn.ensemble import RandomForestClassifier
forest = RandomForestClassifier(n_estimators=5, random_state=2)
forest.fit(X, y)
prediction = forest.predict(test_X)
collections.Counter(prediction)
result = pd.DataFrame({'applied':prediction})
result.to_csv('predict_RandomForest.csv',index=False)

<ipython-input-81-1b687377a9f0>:3: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  forest.fit(X, y)
